# Testing Run Length Encoding


## Imports


In [1]:
from collections import deque
from importlib.util import spec_from_loader, module_from_spec
from importlib.machinery import SourceFileLoader
from scipy.io import wavfile
from glob import glob
import numpy as np
import pandas as pd

# Import Encode
spec = spec_from_loader("encode", SourceFileLoader("encode", "../../encode"))
encode = module_from_spec(spec)
spec.loader.exec_module(encode)

# Import Decode
spec = spec_from_loader("decode", SourceFileLoader("decode", "../../decode"))
decode = module_from_spec(spec)
spec.loader.exec_module(decode)

## Function Definitions


In [2]:
def run_length_encoding_algorithm(rle_l_raw: list):
    """This algorithm will search for contiguous values within the
       array. When the rle_location_count is greater than the value
       65530, the count is reduced by this value in order to
       prevent an overflow of an unsigned 16-bit integer. This allows
       for the data to be stored with 2 bytes when the format of the
       array is a known value in advance of decoding this format. The
       choice of integer 65530 is an arbitrary value less than that of
       the maximum value of an unsigned 16-bit integer (65536).

    Args:
        rle_l_raw (list): This is a list of integer values to be
                          encoded.

    Returns:
        index_array (list): This is the list of run length encoded
                            values.
        rle_locations (list): This is a list of locations of elements
                              that are repeated that are present in the
                              array of indices.
    """
    initial_index = 0
    second_index = 1
    count = 0
    index_array = []
    rle_locations = []
    rle_location_count = 0

    while second_index < len(rle_l_raw):
        if rle_l_raw[initial_index] == rle_l_raw[second_index]:
            index_array.append(rle_l_raw[initial_index])
            rle_locations.append(rle_location_count)

            # continue searching the breadth of the array; increasing
            # count
            while (
                second_index <= len(rle_l_raw)
                and rle_l_raw[initial_index] == rle_l_raw[second_index]
            ):
                count += 1
                second_index += 1
            index_array.append(count)
            if rle_location_count > 65530:
                rle_location_count -= 65530
                rle_location_count += 2
            else:
                rle_location_count += 2
        else:
            index_array.append(rle_l_raw[initial_index])
            if rle_location_count <= 65530:
                rle_location_count += 1
            else:
                rle_location_count -= 65530
                rle_location_count += 1
        count = 0
        initial_index = second_index
        second_index += 1
    if rle_l_raw[-1] != index_array[-2]:
        index_array.append(rle_l_raw[-1])
    return index_array, rle_locations

## Import Data & Huffman Encode Values


In [3]:
data_dir = "../../data/"
data_file_l = glob(data_dir + "*.wav")
current_file = data_file_l[0]

rate, data = wavfile.read(current_file)

data_bytes = data.tobytes()

compressed_file_path = "../../data/102b47d9-371e-412a-8995-0dc6115ab2bb.wav.brainwire"

encode.huffman_encoding(
    input_data=data_bytes,
    compressed_file_path="../../data/102b47d9-371e-412a-8995-0dc6115ab2bb.wav.brainwire",
)

with open(compressed_file_path, "rb") as fp:
    data_huffman_encoded_bytes = fp.read()
    fp.close()

# type(data_huffman_encoded_bytes)

In [4]:
for byte in data_huffman_encoded_bytes[:12]:
    print(byte)

128
4
149
135
5
0
0
0
0
0
0
125


In [5]:
data_huffman_encoded_bytes_sub_string = data_huffman_encoded_bytes

rle_l_raw = []
for data in data_huffman_encoded_bytes_sub_string:
    rle_l_raw.append(data)
rle_l_raw = deque(rle_l_raw)
rle_l_raw

deque([128,
       4,
       149,
       135,
       5,
       0,
       0,
       0,
       0,
       0,
       0,
       125,
       148,
       40,
       140,
       2,
       50,
       48,
       148,
       140,
       4,
       48,
       48,
       48,
       48,
       148,
       140,
       2,
       48,
       56,
       148,
       140,
       5,
       48,
       48,
       48,
       49,
       48,
       148,
       140,
       2,
       48,
       101,
       148,
       140,
       8,
       48,
       48,
       48,
       49,
       49,
       48,
       48,
       48,
       148,
       140,
       2,
       53,
       101,
       148,
       140,
       8,
       48,
       48,
       48,
       49,
       49,
       48,
       48,
       49,
       148,
       140,
       2,
       48,
       102,
       148,
       140,
       9,
       48,
       48,
       48,
       49,
       49,
       48,
       49,
       48,
       48,
       148,
       140,
       2,


In [6]:
index_array, rle_locations = run_length_encoding_algorithm(rle_l_raw)

In [7]:
# Initial Array
rle_l_raw

deque([128,
       4,
       149,
       135,
       5,
       0,
       0,
       0,
       0,
       0,
       0,
       125,
       148,
       40,
       140,
       2,
       50,
       48,
       148,
       140,
       4,
       48,
       48,
       48,
       48,
       148,
       140,
       2,
       48,
       56,
       148,
       140,
       5,
       48,
       48,
       48,
       49,
       48,
       148,
       140,
       2,
       48,
       101,
       148,
       140,
       8,
       48,
       48,
       48,
       49,
       49,
       48,
       48,
       48,
       148,
       140,
       2,
       53,
       101,
       148,
       140,
       8,
       48,
       48,
       48,
       49,
       49,
       48,
       48,
       49,
       148,
       140,
       2,
       48,
       102,
       148,
       140,
       9,
       48,
       48,
       48,
       49,
       49,
       48,
       49,
       48,
       48,
       148,
       140,
       2,


In [8]:
print(f"rle_encoded_value: {index_array[rle_locations[0]]}")
print(f"rle_encoded_frequency: {index_array[rle_locations[0] + 1]}")

rle_encoded_value: 0
rle_encoded_frequency: 5


In [9]:
rle_locations[0]

5

In [11]:
reconstructed_array = []
rle_index = 0
continue_current_index_past_frequency_value = False

for current_index in range(0, len(index_array)):
    if current_index == 5:
        print("breakpoint")
    if continue_current_index_past_frequency_value:
        continue_current_index_past_frequency_value = False
        continue
    if current_index != rle_locations[rle_index]:
        reconstructed_array.append(index_array[current_index])
    else:
        for counter in range(0, index_array[rle_locations[rle_index] + 1]):
            reconstructed_array.append(index_array[rle_locations[rle_index]])
        rle_index += 1
        continue_current_index_past_frequency_value = True

breakpoint


In [12]:
for index in rle_l_raw:
    if rle_l_raw[index] != reconstructed_array[index]:
        print(f"Reconstructed Array is unequal at position: {index}")

Reconstructed Array is unequal at position: 128
Reconstructed Array is unequal at position: 135
Reconstructed Array is unequal at position: 40
Reconstructed Array is unequal at position: 140
Reconstructed Array is unequal at position: 50
Reconstructed Array is unequal at position: 48
Reconstructed Array is unequal at position: 140
Reconstructed Array is unequal at position: 48
Reconstructed Array is unequal at position: 48
Reconstructed Array is unequal at position: 48
Reconstructed Array is unequal at position: 48
Reconstructed Array is unequal at position: 140
Reconstructed Array is unequal at position: 48
Reconstructed Array is unequal at position: 56
Reconstructed Array is unequal at position: 140
Reconstructed Array is unequal at position: 48
Reconstructed Array is unequal at position: 48
Reconstructed Array is unequal at position: 48
Reconstructed Array is unequal at position: 49
Reconstructed Array is unequal at position: 48
Reconstructed Array is unequal at position: 140
Recons

In [27]:
rle_locations

array([    5,    17,    27,    39,    41,    43,    53,    55,    57,
          68,    70,    74,    84,    86,   100,   102,   105,   116,
         118,   121,   126,   131,   133,   143,   155,   157,   168,
         170,   182,   208,   219,   221,   232,   236,   247,   262,
         265,   276,   288,   290,   301,   314,   325,   336,   348,
         362,   375,   389,   404,   406,   420,   422,   435,   449,
         455,   463,   466,   479,   482,   485,   498,   501,   509,
         517,   520,   522,   535,   551,   553,   566,   585,   592,
         605,   607,   619,   633,   643,   645,   655,   657,   669,
         671,   673,   683,   696,   699,   709,   711,   721,   733,
         735,   745,   747,   758,   760,   763,   773,   775,   780,
         790,   792,   797,   808,   810,   817,   827,   829,   836,
         848,   850,   857,   859,   869,   871,   888,   890,   896,
         906,   908,   912,   922,   924,   926,   937,   939,   941,
         943,   953,

In [19]:
index_array[:30]

[128,
 4,
 149,
 135,
 5,
 0,
 5,
 125,
 148,
 40,
 140,
 2,
 50,
 48,
 148,
 140,
 4,
 48,
 3,
 148,
 140,
 2,
 48,
 56,
 148,
 140,
 5,
 48,
 2,
 49]

In [20]:
type(rle_locations)

list

In [21]:
rle_locations = np.array(rle_locations, dtype=np.uint16)
rle_locations_pd = pd.DataFrame(rle_locations)
rle_locations_pd.head()

0
0   5
1  17
2  27
3  39
4  41

## Recreating the array of indices


In [21]:
# reconstructed_array

In [22]:
rle_locations.max()

65404

In [23]:
index_array[rle_locations[0] + 1]

5

In [24]:
rle_locations

array([    5,    17,    27,    39,    41,    43,    53,    55,    57,
          68,    70,    74,    84,    86,   100,   102,   105,   116,
         118,   121,   126,   131,   133,   143,   155,   157,   168,
         170,   182,   208,   219,   221,   232,   236,   247,   262,
         265,   276,   288,   290,   301,   314,   325,   336,   348,
         362,   375,   389,   404,   406,   420,   422,   435,   449,
         455,   463,   466,   479,   482,   485,   498,   501,   509,
         517,   520,   522,   535,   551,   553,   566,   585,   592,
         605,   607,   619,   633,   643,   645,   655,   657,   669,
         671,   673,   683,   696,   699,   709,   711,   721,   733,
         735,   745,   747,   758,   760,   763,   773,   775,   780,
         790,   792,   797,   808,   810,   817,   827,   829,   836,
         848,   850,   857,   859,   869,   871,   888,   890,   896,
         906,   908,   912,   922,   924,   926,   937,   939,   941,
         943,   953,

In [ ]:
print(f"The value that is run length encoded: {index_array[rle_locations[0]]}")
print(f"The number of values detected for run length encoding: ", end="")
print(f"{index_array[rle_locations[0] + 1]}")

In [64]:
rle_locations = np.array(rle_locations)

In [65]:
index_array_1 = index_array[:65536]
index_array_2 = index_array[65536:]

In [66]:
rle_locations_pd = pd.DataFrame(rle_locations)
rle_locations_pd.columns = ["Value"]

rle_locations_2 = (
    rle_locations_pd.where(rle_locations_pd["Value"] >= 65536).dropna().values
)

rle_locations_2 = rle_locations_2.reshape(rle_locations_2.shape[0])
rle_locations_2 = rle_locations_2[:] - 65536
rle_locations_2 = np.array(rle_locations_2, dtype=np.int16)

In [87]:
values_pd = rle_locations_pd.where(rle_locations_pd["Value"] < 65536).dropna()
sample_value = values_pd["Value"].iloc[-1]

In [ ]:
np.array(sample_value, dtype=np.uint16)

In [ ]:
sample_value

In [ ]:
np.array(rle_locations_pd["Value"][:65536], dtype=np.uint16)

In [77]:
rle_locations_1 = (
    rle_locations_pd.where(rle_locations_pd["Value"] < 65536).dropna().values
)
rle_locations_1 = rle_locations_1.reshape(rle_locations_1.shape[0])
rle_locations_1 = np.array(rle_locations_1, dtype=np.uint16)

In [ ]:
rle_locations_1

In [18]:
# Create a list of values such that the indices indicate the positions
# of rle elements that are present in the array of values.

In [ ]:
rle_positions = []
for index in range(1, len(index_array), 2):
    if index_array[index] > 1:
        rle_positions.append(index)
rle_positions

In [ ]:
for item, value in enumerate(rle_positions):
    print(index_array[value])